In [2]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, GridSearchCV
import onnxruntime as rt
import onnx
import xgboost as xgb
from skl2onnx.common.data_types import FloatTensorType
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import SelectFromModel
from sklearn.utils.class_weight import compute_class_weight
from sklearn.metrics import accuracy_score, classification_report
from sklearn.pipeline import Pipeline
from skl2onnx import convert_sklearn

In [3]:
# Load the dataset
data = pd.read_csv('data/synth_data_for_training.csv')


# Separate features / label
y = data['checked']
X = data.drop(['checked'], axis=1)
X = X.astype(np.float32)

# Split into train / test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [60]:
# Select important features
selector = SelectFromModel(RandomForestClassifier(class_weight='balanced'))

In [61]:
# Use XGBoost as classifier
classifier = xgb.XGBClassifier(objective='binary:logistic')

In [62]:
# Create a pipeline object with our selector and classifier
pipeline = Pipeline(steps=[('feature_selection', selector), ('classification', classifier)])

In [63]:
# Cross-validate pipeline
# Define the parameter grid for grid search
param_grid = {
    'feature_selection__max_features': [50, 75, 100],
    'classification__learning_rate': [0.1, 0.2, 0.3],
}

# Create a GridSearchCV object with the pipeline and parameter grid
grid_search = GridSearchCV(pipeline, param_grid, scoring= 'roc_auc', cv=5, verbose= 2)

# Perform grid search with cross-validation
grid_search.fit(X, y)

# Print the best parameters found
print("Best Parameters:", grid_search.best_params_)

# Print the best cross-validation score
print("Best Cross-Validation Score:", grid_search.best_score_)

Fitting 5 folds for each of 9 candidates, totalling 45 fits
[CV] END classification__learning_rate=0.1, feature_selection__max_features=50; total time=   4.2s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=50; total time=   4.0s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=50; total time=   4.3s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=50; total time=   4.1s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=50; total time=   4.3s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=75; total time=   4.2s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=75; total time=   4.3s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=75; total time=   4.3s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=75; total time=   4.4s
[CV] END classification__learning_rate=0.1, featu

In [64]:
# Update pipeline
pipeline.named_steps['classification'].set_params(learning_rate= grid_search.best_params_['classification__learning_rate'])
pipeline.named_steps['feature_selection'].set_params(max_features= grid_search.best_params_['feature_selection__max_features'])

#Fit the model
pipeline.fit(X_train, y_train)
             
# Evaluate the model
y_pred = pipeline.predict(X_test)
original_accuracy = accuracy_score(y_test, y_pred)
print(classification_report(y_test, y_pred))
print('Accuracy of the original model: ', original_accuracy)

              precision    recall  f1-score   support

           0       0.95      0.99      0.97      2278
           1       0.84      0.56      0.67       251

    accuracy                           0.95      2529
   macro avg       0.90      0.77      0.82      2529
weighted avg       0.94      0.95      0.94      2529

Accuracy of the original model:  0.9458283906682483


In [67]:
from skl2onnx import update_registered_converter
from skl2onnx.common.shape_calculator import calculate_linear_classifier_output_shapes  # noqa
from onnxmltools.convert.xgboost.operator_converters.XGBoost import convert_xgboost  # noqa

update_registered_converter(
    xgb.XGBClassifier,
    "XGBoostClassifier",
    calculate_linear_classifier_output_shapes,
    convert_xgboost,
    options={"nocl": [True, False], "zipmap": [True, False, "columns"]}
)
# Convert the model to ONNX
onnx_model = convert_sklearn(
    pipeline, initial_types=[('X', FloatTensorType((None, X.shape[1])))],
    target_opset=12)

# Check the accuracy of the converted model
sess = rt.InferenceSession(onnx_model.SerializeToString())
y_pred_onnx =  sess.run(None, {'X': X_test.values.astype(np.float32)})

accuracy_onnx_model = accuracy_score(y_test, y_pred_onnx[0])
print('Accuracy of the ONNX model: ', accuracy_onnx_model)

Accuracy of the ONNX model:  0.9458283906682483


In [68]:
# Save the model
onnx.save(onnx_model, "model/model_1.onnx")

# Load the model
new_session = rt.InferenceSession("model/model_1.onnx")

# Predict the target
y_pred_onnx2 =  new_session.run(None, {'X': X_test.values.astype(np.float32)})

accuracy_onnx_model = accuracy_score(y_test, y_pred_onnx2[0])
print('Accuracy of the ONNX model: ', accuracy_onnx_model)

Accuracy of the ONNX model:  0.9458283906682483


In [69]:
import giskard

# Replace this with your own data & model creation.
df = giskard.demo.titanic_df()
demo_data_processing_function, demo_sklearn_model = giskard.demo.titanic_pipeline()

# Wrap your Pandas DataFrame with Giskard.Dataset (test set, a golden dataset, etc.).
giskard_dataset = giskard.Dataset(
    df=data,  # A pandas.DataFrame that contains the raw data (before all the pre-processing steps) and the actual ground truth variable (target).
    target="checked",  # Ground truth variable
)

giskard_model = giskard.Model(
    model=pipeline,  # A prediction function that encapsulates all the data pre-processing steps and that could be executed with the dataset used by the scan.
    model_type="classification",  # Either regression, classification or text_generation.
    name="Test",  # Optional
    classification_labels=[0, 1],  # Their order MUST be identical to the prediction_function's output order
)

2024-03-17 21:55:09,993 pid:16288 MainThread giskard.datasets.base INFO     Your 'pandas.DataFrame' is successfully wrapped by Giskard's 'Dataset' wrapper class.
2024-03-17 21:55:10,661 pid:16288 MainThread giskard.models.automodel INFO     Your 'model' is successfully wrapped by Giskard's 'SKLearnModel' wrapper class.


In [70]:
scan_results = giskard.scan(giskard_model, giskard_dataset)

2024-03-17 21:55:24,083 pid:16288 MainThread giskard.datasets.base INFO     Casting dataframe columns from {'adres_aantal_brp_adres': 'int64', 'adres_aantal_verschillende_wijken': 'int64', 'adres_aantal_verzendadres': 'int64', 'adres_aantal_woonadres_handmatig': 'int64', 'adres_dagen_op_adres': 'int64', 'adres_recentst_onderdeel_rdam': 'int64', 'adres_recentste_buurt_groot_ijsselmonde': 'int64', 'adres_recentste_buurt_nieuwe_westen': 'int64', 'adres_recentste_buurt_other': 'int64', 'adres_recentste_buurt_oude_noorden': 'int64', 'adres_recentste_buurt_vreewijk': 'int64', 'adres_recentste_plaats_other': 'int64', 'adres_recentste_plaats_rotterdam': 'int64', 'adres_recentste_wijk_charlois': 'int64', 'adres_recentste_wijk_delfshaven': 'int64', 'adres_recentste_wijk_feijenoord': 'int64', 'adres_recentste_wijk_ijsselmonde': 'int64', 'adres_recentste_wijk_kralingen_c': 'int64', 'adres_recentste_wijk_noord': 'int64', 'adres_recentste_wijk_other': 'int64', 'adres_recentste_wijk_prins_alexa': 'in

C:\Users\alexd\.virtualenvs\ModelTesting-Rom7SsEP\Lib\site-packages\giskard\scanner\scanner.py:258: UserWarning: It looks like your dataset has a very large number of features (315), are you sure this is correct? The giskard.Dataset should be created from raw data *before* pre-processing (categorical encoding, vectorization, etc.). You can also limit the number of features to scan by setting the `features` argument. Check https://docs.giskard.ai/en/latest/guides/wrap_dataset/index.html for more details.
  warning(


2024-03-17 21:55:27,022 pid:16288 MainThread giskard.datasets.base INFO     Casting dataframe columns from {'adres_aantal_brp_adres': 'int64', 'adres_aantal_verschillende_wijken': 'int64', 'adres_aantal_verzendadres': 'int64', 'adres_aantal_woonadres_handmatig': 'int64', 'adres_dagen_op_adres': 'int64', 'adres_recentst_onderdeel_rdam': 'int64', 'adres_recentste_buurt_groot_ijsselmonde': 'int64', 'adres_recentste_buurt_nieuwe_westen': 'int64', 'adres_recentste_buurt_other': 'int64', 'adres_recentste_buurt_oude_noorden': 'int64', 'adres_recentste_buurt_vreewijk': 'int64', 'adres_recentste_plaats_other': 'int64', 'adres_recentste_plaats_rotterdam': 'int64', 'adres_recentste_wijk_charlois': 'int64', 'adres_recentste_wijk_delfshaven': 'int64', 'adres_recentste_wijk_feijenoord': 'int64', 'adres_recentste_wijk_ijsselmonde': 'int64', 'adres_recentste_wijk_kralingen_c': 'int64', 'adres_recentste_wijk_noord': 'int64', 'adres_recentste_wijk_other': 'int64', 'adres_recentste_wijk_prins_alexa': 'in

In [71]:
display(scan_results)

<iframe id="scan-2172899629712" srcdoc="<!doctype html>
<html lang="en">

<head>
 <title>Giskard Scan Results</title>
 <base target="_blank">
 <meta charset="utf-8">
 
<style>pre code.hljs{display:block;overflow-x:auto;padding:1em}code.hljs{padding:3px 5px}
/*!
 Theme: GitHub Dark
 Description: Dark theme as seen on github.com
 Author: github.com
 Maintainer: @Hirse
 Updated: 2021-05-15

 Outdated base version: https://github.com/primer/github-syntax-dark
 Current colors taken from GitHub's CSS
*/.hljs{background:#0d1117;color:#c9d1d9}.hljs-doctag,.hljs-keyword,.hljs-meta .hljs-keyword,.hljs-template-tag,.hljs-template-variable,.hljs-type,.hljs-variable.language_{color:#ff7b72}.hljs-title,.hljs-title.class_,.hljs-title.class_.inherited__,.hljs-title.function_{color:#d2a8ff}.hljs-attr,.hljs-attribute,.hljs-literal,.hljs-meta,.hljs-number,.hljs-operator,.hljs-selector-attr,.hljs-selector-class,.hljs-selector-id,.hljs-variable{color:#79c0ff}.hljs-meta .hljs-string,.hljs-regexp,.hljs-string{color:#a5d6ff}.hljs-built_in,.hljs-symbol{color:#ffa657}.hljs-code,.hljs-comment,.hljs-formula{color:#8b949e}.hljs-name,.hljs-quote,.hljs-selector-pseudo,.hljs-selector-tag{color:#7ee787}.hljs-subst{color:#c9d1d9}.hljs-section{color:#1f6feb;font-weight:700}.hljs-bullet{color:#f2cc60}.hljs-emphasis{color:#c9d1d9;font-style:italic}.hljs-strong{color:#c9d1d9;font-weight:700}.hljs-addition{background-color:#033a16;color:#aff5b4}.hljs-deletion{background-color:#67060c;color:#ffdcd7}.hljs-copy-wrapper{overflow:hidden;position:relative}.hljs-copy-button:focus,.hljs-copy-wrapper:hover .hljs-copy-button{transform:translateX(0)}.hljs-copy-button{background-color:#2d2b57;background-color:var(--hljs-theme-background);background-image:url('data:image/svg+xml;charset=utf-8,<svg xmlns="http://www.w3.org/2000/svg" width="16" height="16" fill="none" viewBox="0 0 24 24"><path fill="%23fff" fill-rule="evenodd" d="M6 5a1 1 0 0 0-1 1v14a1 1 0 0 0 1 1h12a1 1 0 0 0 1-1V6a1 1 0 0 0-1-1h-2a1 1 0 1 1 0-2h2a3 3 0 0 1 3 3v14a3 3 0 0 1-3 3H6a3 3 0 0 1-3-3V6a3 3 0 0 1 3-3h2a1 1 0 0 1 0 2H6Z" clip-rule="evenodd"/><path fill="%23fff" fill-rule="evenodd" d="M7 3a2 2 0 0 1 2-2h6a2 2 0 0 1 2 2v2a2 2 0 0 1-2 2H9a2 2 0 0 1-2-2V3Zm8 0H9v2h6V3Z" clip-rule="evenodd"/></svg>');background-position:50%;background-repeat:no-repeat;border:1px solid #ffffff22;border-radius:.25rem;color:#fff;height:2rem;position:absolute;right:1em;text-indent:-9999px;top:1em;transition:background-color .2s ease,transform .2s ease-out;width:2rem}.hljs-copy-button:hover{border-color:#ffffff44}.hljs-copy-button:active{border-color:#ffffff66}.hljs-copy-button[data-copied=true]{background-image:none;text-indent:0;width:auto}@media (prefers-reduced-motion){.hljs-copy-button{transition:none}}.hljs-copy-alert{clip:rect(0 0 0 0);-webkit-clip-path:inset(50%);clip-path:inset(50%);height:1px;overflow:hidden;position:absolute;white-space:nowrap;width:1px}
/*! tailwindcss v3.3.2 | MIT License | https://tailwindcss.com*/*,:after,:before{border:0 solid #e5e7eb;box-sizing:border-box}:after,:before{--tw-content:""}html{-webkit-text-size-adjust:100%;font-feature-settings:normal;font-family:ui-sans-serif,system-ui,-apple-system,BlinkMacSystemFont,Segoe UI,Roboto,Helvetica Neue,Arial,Noto Sans,sans-serif,Apple Color Emoji,Segoe UI Emoji,Segoe UI Symbol,Noto Color Emoji;font-variation-settings:normal;line-height:1.5;-moz-tab-size:4;-o-tab-size:4;tab-size:4}body{line-height:inherit;margin:0}hr{border-top-width:1px;color:inherit;height:0}abbr:where([title]){-webkit-text-decoration:underline dotted;text-decoration:underline dotted}h1,h2,h3,h4,h5,h6{font-size:inherit;font-weight:inherit}a{color:inherit;text-decoration:inherit}b,strong{font-weight:bolder}code,kbd,pre,samp{font-family:ui-monospace,SFMono-Regular,Menlo,Monaco,Consolas,Liberation Mono,Courier New,monospace;font-size:1em}small{font-size:80%}sub,sup{font-size:75%;line-height:0;position:relative;vertical-align:baseline}sub{bottom:-.25em}sup{top:-.5em}table{border-collapse: